In [219]:
import pandas as pd
import sys

import plotly.graph_objects as go

In [218]:
# Connection parameters
from pyhive import hive
host_name = "192.168.153.130"
port = 10000
user = "hive"
conn = hive.Connection(host=host_name, port=port, username=user, auth='NOSASL')
# modified /etc/hive/conf/conf.xml to add NOSASL propery

In [220]:
# Q1: how many different currencies are we considering in our data set ?
df = pd.read_sql("SELECT count(*), currency FROM default.crypto_hive_4 GROUP BY currency", conn) 
df.head()
df.columns = ['count', 'currency']

C:\Users\Student\AppData\Local\Temp\ipykernel_14928\29487577.py:2: UserWarning:

pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.



In [194]:
colors = ['gold', 'mediumturquoise', 'darkorange', 'lightgreen']
fig = go.Figure(data=[go.Pie(labels=df['currency'],
                             values=df['count'])])
fig.update_traces(hoverinfo='label+percent', textinfo='value', textfont_size=20,
                  marker=dict(colors=colors, line=dict(color='#000000', width=2)))
fig.show()

In [229]:
# q2: what is the most recent high price for "btc" ?
df_btc = pd.read_sql("SELECT * FROM crypto_hive_4 where currency ='btc' order by time DESC", conn) 
print(sys.getsizeof(df_btc))
df_btc.head()

C:\Users\Student\AppData\Local\Temp\ipykernel_14928\685341632.py:2: UserWarning:

pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.



19540480


crypto_hive_4.key crypto_hive_4.currency crypto_hive_4.time   
0  btc-1530874080000                    btc      1530874080000  \
1  btc-1530874020000                    btc      1530874020000   
2  btc-1530873960000                    btc      1530873960000   
3  btc-1530873900000                    btc      1530873900000   
4  btc-1530873840000                    btc      1530873840000   

  crypto_hive_4.open crypto_hive_4.close crypto_hive_4.high crypto_hive_4.low   
0             6532.2              6528.1             6532.2            6526.2  \
1             6537.0              6533.6             6537.0            6527.3   
2             6524.6              6539.0             6544.3            6524.6   
3             6521.5              6524.5             6524.5            6521.5   
4             6521.4              6521.5             6521.5            6521.4   

  crypto_hive_4.volume crypto_hive_4.create_time  
0           1.41598966             1682266302056  
1          59.59326327             1682266302055  
2         123.14929927             1682266302043  
3           1.54590071             1682266302042  
4           3.41745683             1682266302042

In [230]:
df_btc.columns = ["key", "curr", "time", "open","close","high", "low", "vol", "create_time"]

In [231]:
df_btc.count()

key            32851
curr           32851
time           32851
open           32851
close          32851
high           32851
low            32851
vol            32851
create_time    32851
dtype: int64

In [232]:
from time import strftime, localtime
df_btc['date_time'] = df_btc.apply(lambda x: strftime('%Y-%m-%d %H:%M:%S', localtime(int(x['time'])/1000)), axis=1)


In [233]:
df_btc['high'] = df_btc["high"].apply(lambda x: round(float(x),2));

In [234]:
df_btc.head()

key curr           time    open   close    high     low   
0  btc-1530874080000  btc  1530874080000  6532.2  6528.1  6532.2  6526.2  \
1  btc-1530874020000  btc  1530874020000  6537.0  6533.6  6537.0  6527.3   
2  btc-1530873960000  btc  1530873960000  6524.6  6539.0  6544.3  6524.6   
3  btc-1530873900000  btc  1530873900000  6521.5  6524.5  6524.5  6521.5   
4  btc-1530873840000  btc  1530873840000  6521.4  6521.5  6521.5  6521.4   

            vol    create_time            date_time  
0    1.41598966  1682266302056  2018-07-06 05:48:00  
1   59.59326327  1682266302055  2018-07-06 05:47:00  
2  123.14929927  1682266302043  2018-07-06 05:46:00  
3    1.54590071  1682266302042  2018-07-06 05:45:00  
4    3.41745683  1682266302042  2018-07-06 05:44:00

In [238]:
import datetime as dt

In [235]:
df_btc_final = df_btc.filter(items=['curr', 'date_time', 'high'])

In [256]:
df_btc_final['date_time'] = pd.to_datetime(df_btc_final.date_time)
df_btc_final['date_time'].loc[df_btc_final['date_time'].dt.year==2015]

Series([], Name: date_time, dtype: datetime64[ns])

In [262]:
df_2018 = df_btc_final.loc[df_btc_final['date_time'].dt.year==2018]

In [263]:
fig = go.Figure([go.Scatter(x=df_2018['date_time'], y=df_2018['high'])])
fig.show()

In [258]:
import plotly.express as px
fig = px.scatter(x=df_btc_final['date_time'], y=df_btc_final['high'])
fig.show()

In [217]:
df_btc = pd.read_sql("SELECT currency, time, high FROM default.crypto_hive_4 WHERE currency='btc' ORDER BY time DESC", conn)     
time = df_btc.loc[0]['time']
previous_high = df_btc.loc[0]['high'] 
currency = 'btc'

C:\Users\Student\AppData\Local\Temp\ipykernel_14928\2182114449.py:1: UserWarning:

pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.



KeyboardInterrupt: 

In [216]:
import datetime

import dash
from dash import dcc, html
import plotly
from dash.dependencies import Input, Output

# pip install pyorbital
from pyorbital.orbital import Orbital
satellite = Orbital('TERRA')

external_stylesheets = ['https://codepen.io/chriddyp/pen/bWLwgP.css']

app = dash.Dash(__name__, external_stylesheets=external_stylesheets)
app.layout = html.Div(
    html.Div([
        html.H4('Live Feed'),
        html.Div(id='live-update-text'),
#         dcc.Graph(id='live-update-graph'),
        dcc.Interval(
            id='interval-component',
            interval=60*1000, # in milliseconds
            n_intervals=0
        )
    ])
)


@app.callback(Output('live-update-text', 'children'),
              Input('interval-component', 'n_intervals'))
def update_metrics(n):
    df_btc = pd.read_sql("SELECT currency, time, high FROM default.crypto_hive_4 WHERE currency='btc' ORDER BY time DESC", conn)     
    time = df_btc.loc[0]['time']
    previous_high = df_btc.loc[0]['high'] 
    currency = 'btc'
#     lon, lat, alt = satellite.get_lonlatalt(datetime.datetime.now())
    style = {'padding': '5px', 'fontSize': '16px'}
    return [
        html.Span('currency:'.format(currency), style=style),
        html.Span('previous_high: '.format(previous_high), style=style),
        html.Span('time:'.format(time), style=style)
    ]


# Multiple components can update everytime interval gets fired.
# @app.callback(Output('live-update-graph', 'figure'),
#               Input('interval-component', 'n_intervals'))
# def update_graph_live(n):
#     satellite = Orbital('TERRA')
#     data = {
#         'time': [],
#         'Latitude': [],
#         'Longitude': [],
#         'Altitude': []
#     }

#     # Collect some data
#     for i in range(180):
#         time = datetime.datetime.now() - datetime.timedelta(seconds=i*20)
#         lon, lat, alt = satellite.get_lonlatalt(
#             time
#         )
#         data['Longitude'].append(lon)
#         data['Latitude'].append(lat)
#         data['Altitude'].append(alt)
#         data['time'].append(time)

#     # Create the graph with subplots
#     fig = plotly.tools.make_subplots(rows=2, cols=1, vertical_spacing=0.2)
#     fig['layout']['margin'] = {
#         'l': 30, 'r': 10, 'b': 30, 't': 10
#     }
#     fig['layout']['legend'] = {'x': 0, 'y': 1, 'xanchor': 'left'}

#     fig.append_trace({
#         'x': data['time'],
#         'y': data['Altitude'],
#         'name': 'Altitude',
#         'mode': 'lines+markers',
#         'type': 'scatter'
#     }, 1, 1)
#     fig.append_trace({
#         'x': data['Longitude'],
#         'y': data['Latitude'],
#         'text': data['time'],
#         'name': 'Longitude vs Latitude',
#         'mode': 'lines+markers',
#         'type': 'scatter'
#     }, 2, 1)

    return fig


if __name__ == '__main__':
    app.run_server(debug=True, use_reloader=False)

Dash is running on http://127.0.0.1:8050/

 * Serving Flask app '__main__'
 * Debug mode: on


C:\Users\Student\AppData\Local\Temp\ipykernel_14928\3207626792.py:32: UserWarning:

pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.



In [183]:
from dash import Dash, dcc, html, Input, Output
import plotly.express as px

app = Dash(__name__)

app.layout = html.Div([
    html.H4('Stock price analysis'),
    dcc.Graph(id="time-series-chart"),
    html.P("Select stock:"),
    dcc.Dropdown(
        id="ticker",
        options=["close", "low", "vol", "open"],
        value="high",
        clearable=False,
    ),
])

@app.callback(
    Output("time-series-chart", "figure"), 
    Input("ticker", "value"))
def display_time_series(ticker):
    fig = px.line(df2, x='date_time', y=ticker)
    return fig

app.run_server(debug=True, use_reloader=False)

Dash is running on http://127.0.0.1:8050/

 * Serving Flask app '__main__'
 * Debug mode: on


In [ ]:
df_efilterd.read_sql("SELECT * FROM crypto_hive_4 order by time DESC limit 100", conn) 
print(sys.getsizeof(df2))
df2.head()

In [185]:
# plot 3: different plots for same date time



fig = px.line(df, x="year", y="lifeExp", color='country')
fig.show()

Dash is running on http://127.0.0.1:8050/

 * Serving Flask app '__main__'
 * Debug mode: on


In [153]:
# how many crytocurrencies data are we analyzing ? 


colors = ['gold', 'mediumturquoise', 'darkorange', 'lightgreen']

fig = go.Figure(data=[go.Pie(labels=list(dist.keys()),
                             values=list(dist.values()))])
fig.update_traces(hoverinfo='label+percent', textinfo='value', textfont_size=20,
                  marker=dict(colors=colors, line=dict(color='#000000', width=2)))
fig.show()

In [116]:
df

crypto_hive.key crypto_hive.currency crypto_hive.time   
0     doge-1628647620000                 doge    1628647620000  \
1     doge-1628647560000                 doge    1628647560000   
2     doge-1628647500000                 doge    1628647500000   
3     doge-1628647440000                 doge    1628647440000   
4     doge-1628647380000                 doge    1628647380000   
...                  ...                  ...              ...   
1591   btc-1364775120000                  btc    1364775120000   
1592   btc-1364775060000                  btc    1364775060000   
1593   btc-1364774940000                  btc    1364774940000   
1594   btc-1364774880000                  btc    1364774880000   
1595   btc-1364774820000                  btc    1364774820000   

     crypto_hive.open crypto_hive.close crypto_hive.high crypto_hive.low   
0             0.26233            0.2626          0.26351         0.26233  \
1             0.26161           0.26231          0.26231         0.26161   
2             0.26139           0.26125          0.26139         0.26061   
3               0.262            0.2614            0.262          0.2614   
4             0.26193           0.26191          0.26231         0.26186   
...               ...               ...              ...             ...   
1591            93.47             93.47            93.47           93.47   
1592            93.35             93.47            93.47           93.35   
1593             93.3              93.3             93.3            93.3   
1594            100.0             100.0            100.0           100.0   
1595            93.25              93.3             93.3           93.25   

      crypto_hive.volume crypto_hive.create_time  
0     6875.8901154000005           1682218489317  
1          20250.8515431           1682218489315  
2          1891.77506782           1682218489313  
3         77083.32058148           1682218489308  
4                20350.0           1682218489306  
...                  ...                     ...  
1591          2.02162704           1682218489329  
1592                20.0           1682218489328  
1593         33.67686227           1682218489326  
1594                93.3           1682218489320  
1595                93.3           1682218489319  

[1596 rows x 9 columns]

In [95]:
df.dropna()

key curr           time          open         close   
0   btc-1364915640000  btc  1364915640000  108.46883206  108.18422222  \
1   btc-1364915580000  btc  1364915580000   108.4751196   108.4751196   
2   btc-1364915520000  btc  1364915520000  108.40588035  108.40588035   
3   btc-1364915460000  btc  1364915460000  108.40895848  108.40588035   
4   btc-1364914680000  btc  1364914680000        108.05        108.05   
..                ...  ...            ...           ...           ...   
95  btc-1364891280000  btc  1364891280000         103.0         103.0   
96  btc-1364891160000  btc  1364891160000        102.96        102.96   
97  btc-1364891100000  btc  1364891100000        102.96        102.96   
98  btc-1364891040000  btc  1364891040000         102.8        102.95   
99  btc-1364889600000  btc  1364889600000     102.77689     102.77689   

            high           low         vol    create_time  
0   108.46975222  108.08197222        50.0  1682218490344  
1    108.4751196   108.4751196       13.76  1682218490336  
2   108.40588035  108.40588035        2.08  1682218490334  
3   108.40895848  108.40588035        4.16  1682218490333  
4         108.05        108.05        10.0  1682218490332  
..           ...           ...         ...            ...  
95         103.0         103.0        10.0  1682218490084  
96        102.96        102.96     0.49785  1682218490081  
97        102.96        102.96     0.09957  1682218490079  
98        102.95         102.8  1.15669264  1682218490076  
99     102.77689     102.77689   0.0498486  1682218490075  

[100 rows x 9 columns]

In [69]:
df2 = df.loc[df['curr'] == 'eth']
df2

key curr           time    open   close    high     low   
57  eth-1457539440000  eth  1457539440000  10.297  10.097  10.297  10.097  \
58  eth-1457545740000  eth  1457545740000  11.197  11.197  11.197  11.197   
59  eth-1457549760000  eth  1457549760000  11.097  11.097  11.097  11.097   
60  eth-1457554560000  eth  1457554560000  11.195  11.195  11.195  11.195   
61  eth-1457554860000  eth  1457554860000   10.87   10.87   10.87   10.87   
62  eth-1457554980000  eth  1457554980000   10.87   10.66   10.87   10.66   
63  eth-1457560020000  eth  1457560020000   10.87  11.197  11.197   10.87   
64  eth-1457626260000  eth  1457626260000  11.072  11.072  11.072  11.072   
65  eth-1457626320000  eth  1457626320000   11.75   11.75   11.75   11.75   
66  eth-1457631780000  eth  1457631780000   11.85   11.75   11.85   11.75   
67  eth-1457693460000  eth  1457693460000   11.85   11.85   11.85   11.85   
68  eth-1457693580000  eth  1457693580000   11.85   11.85   11.85   11.85   
69  eth-1457693640000  eth  1457693640000   11.85   11.85   11.85   11.85   
70  eth-1457717220000  eth  1457717220000    11.8    11.8    11.8    11.8   
71  eth-1457721900000  eth  1457721900000    11.8    11.8    11.8    11.8   
72  eth-1457733000000  eth  1457733000000   11.95   11.85   11.95   11.85   
73  eth-1457733300000  eth  1457733300000   11.95   11.95   11.95   11.95   
74  eth-1457734980000  eth  1457734980000   11.95   11.95   11.95   11.95   
75  eth-1457735460000  eth  1457735460000   11.95   11.95   11.95   11.95   

                   vol  
57                0.03  
58                0.01  
59                0.02  
60                0.01  
61                 1.0  
62            0.099523  
63                40.0  
64                0.02  
65                0.01  
66                 1.0  
67                0.01  
68                0.01  
69                0.01  
70                0.01  
71  0.7048979999999999  
72  2.9758310000000003  
73              1.0873  
74  2.9758310000000003  
75   4.063130999999999

In [71]:
from time import strftime, localtime
print(strftime('%Y-%m-%d %H:%M:%S', localtime(1457734980000/1000)))


2016-03-11 16:23:00


In [72]:
import datetime
datetime.datetime.fromtimestamp(1457734980).strftime('%c')

'Fri Mar 11 16:23:00 2016'

In [97]:
a = int(df.loc[0]['time'])

In [96]:
print(strftime('%Y-%m-%d %H:%M:%S', localtime(a/1000)))

2020-08-06 05:11:00


In [98]:
df3=df.copy()

In [99]:
df3

key curr           time          open         close   
0   btc-1364915640000  btc  1364915640000  108.46883206  108.18422222  \
1   btc-1364915580000  btc  1364915580000   108.4751196   108.4751196   
2   btc-1364915520000  btc  1364915520000  108.40588035  108.40588035   
3   btc-1364915460000  btc  1364915460000  108.40895848  108.40588035   
4   btc-1364914680000  btc  1364914680000        108.05        108.05   
..                ...  ...            ...           ...           ...   
95  btc-1364891280000  btc  1364891280000         103.0         103.0   
96  btc-1364891160000  btc  1364891160000        102.96        102.96   
97  btc-1364891100000  btc  1364891100000        102.96        102.96   
98  btc-1364891040000  btc  1364891040000         102.8        102.95   
99  btc-1364889600000  btc  1364889600000     102.77689     102.77689   

            high           low         vol    create_time  
0   108.46975222  108.08197222        50.0  1682218490344  
1    108.4751196   108.4751196       13.76  1682218490336  
2   108.40588035  108.40588035        2.08  1682218490334  
3   108.40895848  108.40588035        4.16  1682218490333  
4         108.05        108.05        10.0  1682218490332  
..           ...           ...         ...            ...  
95         103.0         103.0        10.0  1682218490084  
96        102.96        102.96     0.49785  1682218490081  
97        102.96        102.96     0.09957  1682218490079  
98        102.95         102.8  1.15669264  1682218490076  
99     102.77689     102.77689   0.0498486  1682218490075  

[100 rows x 9 columns]

In [111]:
df3['create_time']

0     1682218490344
1     1682218490336
2     1682218490334
3     1682218490333
4     1682218490332
          ...      
95    1682218490084
96    1682218490081
97    1682218490079
98    1682218490076
99    1682218490075
Name: create_time, Length: 100, dtype: object

In [112]:
df3['create_time'] = df3.apply(lambda x: strftime('%Y-%m-%d %H:%M:%S', localtime(int(x['create_time'])/1000)), axis=1)

In [113]:
df3

key curr                 time          open         close   
0   btc-1364915640000  btc  2023-04-22 21:54:50  108.46883206  108.18422222  \
1   btc-1364915580000  btc  2023-04-22 21:54:50   108.4751196   108.4751196   
2   btc-1364915520000  btc  2023-04-22 21:54:50  108.40588035  108.40588035   
3   btc-1364915460000  btc  2023-04-22 21:54:50  108.40895848  108.40588035   
4   btc-1364914680000  btc  2023-04-22 21:54:50        108.05        108.05   
..                ...  ...                  ...           ...           ...   
95  btc-1364891280000  btc  2023-04-22 21:54:50         103.0         103.0   
96  btc-1364891160000  btc  2023-04-22 21:54:50        102.96        102.96   
97  btc-1364891100000  btc  2023-04-22 21:54:50        102.96        102.96   
98  btc-1364891040000  btc  2023-04-22 21:54:50         102.8        102.95   
99  btc-1364889600000  btc  2023-04-22 21:54:50     102.77689     102.77689   

            high           low         vol          create_time  
0   108.46975222  108.08197222        50.0  2023-04-22 21:54:50  
1    108.4751196   108.4751196       13.76  2023-04-22 21:54:50  
2   108.40588035  108.40588035        2.08  2023-04-22 21:54:50  
3   108.40895848  108.40588035        4.16  2023-04-22 21:54:50  
4         108.05        108.05        10.0  2023-04-22 21:54:50  
..           ...           ...         ...                  ...  
95         103.0         103.0        10.0  2023-04-22 21:54:50  
96        102.96        102.96     0.49785  2023-04-22 21:54:50  
97        102.96        102.96     0.09957  2023-04-22 21:54:50  
98        102.95         102.8  1.15669264  2023-04-22 21:54:50  
99     102.77689     102.77689   0.0498486  2023-04-22 21:54:50  

[100 rows x 9 columns]

In [60]:
df3

key curr                 time                open   
0   ada-1596708660000  ada  2475-12-22 23:50:00              0.1427  \
1   ada-1596708900000  ada  2475-12-23 00:30:00             0.14251   
2   ada-1596708960000  ada  2475-12-23 00:40:00             0.14238   
3   ada-1596709140000  ada  2475-12-23 01:10:00             0.14234   
4   ada-1596709620000  ada  2475-12-23 02:30:00  0.1424099999999999   
..                ...  ...                  ...                 ...   
71  eth-1457721900000  eth  2431-12-07 13:30:00                11.8   
72  eth-1457733000000  eth  2431-12-08 20:20:00               11.95   
73  eth-1457733300000  eth  2431-12-08 21:10:00               11.95   
74  eth-1457734980000  eth  2431-12-09 01:50:00               11.95   
75  eth-1457735460000  eth  2431-12-09 03:10:00               11.95   

                 close                high                 low   
0               0.1427              0.1427              0.1427  \
1              0.14251             0.14251             0.14251   
2              0.14238             0.14238             0.14238   
3              0.14234             0.14234             0.14234   
4   0.1424099999999999  0.1424099999999999  0.1424099999999999   
..                 ...                 ...                 ...   
71                11.8                11.8                11.8   
72               11.85               11.95               11.85   
73               11.95               11.95               11.95   
74               11.95               11.95               11.95   
75               11.95               11.95               11.95   

                   vol  
0                 10.0  
1            7557.1124  
2            7678.9949  
3            7773.4923  
4    8118.566999999999  
..                 ...  
71  0.7048979999999999  
72  2.9758310000000003  
73              1.0873  
74  2.9758310000000003  
75   4.063130999999999  

[76 rows x 8 columns]

In [106]:
import plotly.graph_objects as go

import pandas as pd
df = pd.read_csv('https://raw.githubusercontent.com/plotly/datasets/master/finance-charts-apple.csv')

fig = go.Figure([go.Scatter(x=df3['create_time'], y=df3['curr'])])
fig.show()

# fig = go.Figure([go.Scatter(x=df3['time'], y=df['curr'])])

In [33]:
currencies = list(df['curr'].unique())

In [82]:
df2['time'] = df2.apply(lambda x: strftime('%Y-%m-%d %H:%M:%S', localtime(int(x['time'])/1000)), axis=1)

C:\Users\Student\AppData\Local\Temp\ipykernel_14928\1551946363.py:1: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [83]:
import plotly.express as px
fig = px.line(df2, x='time', y='high')
fig.show()

In [26]:
from dash import Dash, dcc, html, Input, Output

app = Dash(__name__)
app.layout = html.Div([
    dcc.Dropdown(currencies, currencies[0], id='demo-dropdown'),
    html.Div(id='dd-output-container')
])


@app.callback(
    Output('dd-output-container', 'children'),
    Input('demo-dropdown', 'value')
)
def update_output(value):
    return f'You have selected {value}'


if __name__ == '__main__':
    app.run_server(debug=True, use_reloader=False)

Dash is running on http://127.0.0.1:8050/

 * Serving Flask app '__main__'
 * Debug mode: on


In [16]:
import datetime

import dash
from dash import dcc, html
import plotly
from dash.dependencies import Input, Output

# pip install pyorbital
from pyorbital.orbital import Orbital
satellite = Orbital('TERRA')

external_stylesheets = ['https://codepen.io/chriddyp/pen/bWLwgP.css']

app = dash.Dash(__name__, external_stylesheets=external_stylesheets)
app.layout = html.Div(
    html.Div([
        html.H4('TERRA Satellite Live Feed'),
        html.Div(id='live-update-text'),
        dcc.Graph(id='live-update-graph'),
        dcc.Interval(
            id='interval-component',
            interval=1*1000, # in milliseconds
            n_intervals=0
        )
    ])
)


@app.callback(Output('live-update-text', 'children'),
              Input('interval-component', 'n_intervals'))
def update_metrics(n):
    lon, lat, alt = satellite.get_lonlatalt(datetime.datetime.now())
    style = {'padding': '5px', 'fontSize': '16px'}
    return [
        html.Span('Longitude: {0:.2f}'.format(lon), style=style),
        html.Span('Latitude: {0:.2f}'.format(lat), style=style),
        html.Span('Altitude: {0:0.2f}'.format(alt), style=style)
    ]


# Multiple components can update everytime interval gets fired.
@app.callback(Output('live-update-graph', 'figure'),
              Input('interval-component', 'n_intervals'))
def update_graph_live(n):
    satellite = Orbital('TERRA')
    data = {
        'time': [],
        'Latitude': [],
        'Longitude': [],
        'Altitude': []
    }

    # Collect some data
    for i in range(180):
        time = datetime.datetime.now() - datetime.timedelta(seconds=i*20)
        lon, lat, alt = satellite.get_lonlatalt(time)
        data['Longitude'].append(lon)
        data['Latitude'].append(lat)
        data['Altitude'].append(alt)
        data['time'].append(time)

    # Create the graph with subplots
    fig = plotly.tools.make_subplots(rows=2, cols=1, vertical_spacing=0.2)
    fig['layout']['margin'] = {
        'l': 30, 'r': 10, 'b': 30, 't': 10
    }
    fig['layout']['legend'] = {'x': 0, 'y': 1, 'xanchor': 'left'}

    fig.append_trace({
        'x': data['time'],
        'y': data['Altitude'],
        'name': 'Altitude',
        'mode': 'lines+markers',
        'type': 'scatter'
    }, 1, 1)
    fig.append_trace({
        'x': data['Longitude'],
        'y': data['Latitude'],
        'text': data['time'],
        'name': 'Longitude vs Latitude',
        'mode': 'lines+markers',
        'type': 'scatter'
    }, 2, 1)

    return fig


if __name__ == '__main__':
    app.run_server(debug=True,use_reloader=False)

Dash is running on http://127.0.0.1:8050/

 * Serving Flask app '__main__'
 * Debug mode: on


c:\users\student\appdata\local\programs\python\python38\lib\site-packages\plotly\tools.py:460: DeprecationWarning:

plotly.tools.make_subplots is deprecated, please use plotly.subplots.make_subplots instead

